# Inspecting the Email Marketing CSV with Recommendation Products

In [103]:
import pandas as pd

In [104]:
df=pd.read_csv("ffinal_Emarketing.csv")

In [105]:
df.head()

customer_id                                            product  \
0         11.0  HQD AIR 5% 1X5PK DISPOSABLE (4000) (Frozen Cho...   
1         14.0  WISE TRASH BAG 10CT/26GALLON BLACK , NUTRAMENT...   
2         46.0      FUME 10PK EXTRA 5% DISPOSABLE (1500)  (Clear)   
3       2391.0  BLAZY CONE PINK 1 1/4 21 PACKS PER BOX , BACKW...   
4       2540.0             GRINDER (GR044-4) 4 PARTS PLASTIC 50MM   

                                Recommended_products   customer_name  \
0  FUME NICKY JAM 10PK (10000) (Summer Amante) , ...  Angelo Difatta   
1  .LOTY COCONUT WATER 24-500ML , LOTY JUICE 24-5...  Nepa Wholesale   
2  VIPER 5PK SUPER 5% (Mint Ice) , ORION BAR 5% 1...   305 VAPES LLC   
3  LOST MARY 10PK 5% (OS5000) (Pineapple Duo) , B...      3KINGZ LLC   
4  Aerospaced By Hs 4 Piece Grinder 63 MM (Gunmet...     BANDARI LLC   

              customer_email        date  last_purchased_month  
0   angelo@nepawholesale.com  2024-02-19                     2  
1  nepawholesale@hotmail.com  2024-05-06                     5  
2      305vapesllc@gmail.com  2024-05-21                     5  
3       3kingzshop@gmail.com  2024-05-16                     5  
4       bandarillc@gmail.com  2024-02-27                     2

In [106]:
df.drop(columns=['last_purchased_month'],inplace=True)

In [107]:
df.head()

customer_id                                            product  \
0         11.0  HQD AIR 5% 1X5PK DISPOSABLE (4000) (Frozen Cho...   
1         14.0  WISE TRASH BAG 10CT/26GALLON BLACK , NUTRAMENT...   
2         46.0      FUME 10PK EXTRA 5% DISPOSABLE (1500)  (Clear)   
3       2391.0  BLAZY CONE PINK 1 1/4 21 PACKS PER BOX , BACKW...   
4       2540.0             GRINDER (GR044-4) 4 PARTS PLASTIC 50MM   

                                Recommended_products   customer_name  \
0  FUME NICKY JAM 10PK (10000) (Summer Amante) , ...  Angelo Difatta   
1  .LOTY COCONUT WATER 24-500ML , LOTY JUICE 24-5...  Nepa Wholesale   
2  VIPER 5PK SUPER 5% (Mint Ice) , ORION BAR 5% 1...   305 VAPES LLC   
3  LOST MARY 10PK 5% (OS5000) (Pineapple Duo) , B...      3KINGZ LLC   
4  Aerospaced By Hs 4 Piece Grinder 63 MM (Gunmet...     BANDARI LLC   

              customer_email        date  
0   angelo@nepawholesale.com  2024-02-19  
1  nepawholesale@hotmail.com  2024-05-06  
2      305vapesllc@gmail.com  2024-05-21  
3       3kingzshop@gmail.com  2024-05-16  
4       bandarillc@gmail.com  2024-02-27

# 1. EMAIL GENERATION

In [108]:
# Importing the libraries
import langchain
from langchain_groq import ChatGroq
from langchain_experimental.agents.agent_toolkits import create_csv_agent
from langchain.prompts import PromptTemplate
import re
from langchain.chains import LLMChain
from langchain_google_genai import ChatGoogleGenerativeAI
import sys
import ast
import pandas as pd

### 1.1 Defining LLM MODEL

In [109]:
llm = ChatGoogleGenerativeAI(model="gemini-pro", temperature=0.2, google_api_key="")

### 1.2 List of Available Customers 

In [121]:
id_list = ['22086.0']


### 1.3 Definining CSV Agent

In [111]:
def get_dict(llm, csv, ids):
    results = []
    csv_agent = create_csv_agent(llm, csv, verbose=True, allow_dangerous_code=True)
   
    for id in ids:
        query = f"""
        Extract 'customer_id', 'customer_name', 'product', 'Recommended_products', 'customer_email', 'Date', 'last_purchased_month' 
        for 'customer_id' {id} and format it as a dictionary using df[df['customer_id'] == {id}].to_dict('records')[0].
        Ensure the resulting dictionary includes essential fields such as 'customer_name', 'Recommended_products', and 'customer_email'.
        """
       
        ans = csv_agent.invoke(query)
       
        model_output = ans['output']
 
     
        pattern = r"\{.*?\}"
 
        match = re.search(pattern, model_output)
       
        if match:
            dictionary_part = match.group(0)
            dictionary_part = eval(dictionary_part)
            results.append(dictionary_part)
 
    return results
 
dictionary_parts = get_dict(llm, "ffinal_Emarketing.csv", id_list)



> Entering new AgentExecutor chain...
Thought: I should use the df[df['customer_id'] == 22086.0] to filter the dataframe for the customer_id 22086.0 and then use the to_dict('records')[0] to convert it to a dictionary.
Action: python_repl_ast
Action Input: df[df['customer_id'] == 22086.0].to_dict('records')[0]{'customer_id': 22086.0, 'product': 'HQD PLUS 5% 1X6PK DISPOSABLE (1200) (Black Ice) , REMARKABLE HERBS 8OZ POWDER (White Maeng Da) , HQD BAR 5% 1X5PK DISPOSABLE (7000) (Cranberry Grape) , SAVIA 12CT-500ML (Aloe Vera Mango)', 'Recommended_products': "ORION BAR 5% 1X5PK DISPOSABLE (10000) (KIWI PASSION FRUIT GUAVA) , DUMMY XFINITY 5% 1X5PK DISPOSABLE (6900) (Bebe Berry) , JELLY LIVE RESIN KO BLEND GUMMIES 1CT , CLICKIT LIGHTER (GH-10877C) BOB MARLEY TORCH LIGHTER 15CT , HALF BAKD 5-2 CONEZ (Sugar Cookie) , SQUID 5K 5% 1X5PK DISPOSABLE (Blue Razz) , LOST MARY 10PK 5% (OS5000) (Black Lemonade) , CAKE HXC 5PK (Animal Cookies) , TORCH ONYX 5PK UNICORN BUTTER , VIRGINIA SLIMS 120'S BO

### 1.4 Inspecting Dict

In [112]:
dictionary_parts[0]

{'customer_id': 22086.0,
 'product': 'HQD PLUS 5% 1X6PK DISPOSABLE (1200) (Black Ice) , REMARKABLE HERBS 8OZ POWDER (White Maeng Da) , HQD BAR 5% 1X5PK DISPOSABLE (7000) (Cranberry Grape) , SAVIA 12CT-500ML (Aloe Vera Mango)',
 'Recommended_products': "ORION BAR 5% 1X5PK DISPOSABLE (10000) (KIWI PASSION FRUIT GUAVA) , DUMMY XFINITY 5% 1X5PK DISPOSABLE (6900) (Bebe Berry) , JELLY LIVE RESIN KO BLEND GUMMIES 1CT , CLICKIT LIGHTER (GH-10877C) BOB MARLEY TORCH LIGHTER 15CT , HALF BAKD 5-2 CONEZ (Sugar Cookie) , SQUID 5K 5% 1X5PK DISPOSABLE (Blue Razz) , LOST MARY 10PK 5% (OS5000) (Black Lemonade) , CAKE HXC 5PK (Animal Cookies) , TORCH ONYX 5PK UNICORN BUTTER , VIRGINIA SLIMS 120'S BOX (Menthol Gold)",
 'customer_name': 'AAHIL PETROLEUM INC',
 'customer_email': 'anoor8484@gmail.com',
 'date': '2024-06-19',
 'last_purchased_month': 6}

### 1.5 Preparing E-Mail Template

In [113]:
# Provided data
data = dictionary_parts[0]

mail_format = """
Dear {customer_name},

I hope this email finds you well. We truly appreciate your continued trust in NEPA WHOLESALE for your product needs.

We noticed that you've recently purchased the following items from us on {Date}:

{products}
...etc

Based on your preferences, we have curated a selection of products that we believe will perfectly complement and enhance your current offerings:

{recommended_products}

Our goal is to help you continue providing high-quality products to your customers and to support your business growth. Each of these recommendations has been carefully selected to ensure they align with your business needs and market demands.

If you have any questions or need further assistance, please don't hesitate to reach out. We're here to help you make the best choices for your business.

Thank you once again for choosing NEPA WHOLESALE. We look forward to continuing our successful partnership.

Best regards,

NEPA WHOLESALE LLC

"""

# Split the products and recommended products into lists
products_list = data['product'].split(' , ')
recommended_products_list = data['Recommended_products'].split(' , ')

# Add bullets to each item in the lists
products_str = "\n".join(f"• {item}" for item in products_list)
recommended_products_str = "\n".join(f"• {item}" for item in recommended_products_list)

# Fill the placeholders in the email template
formatted_email = mail_format.format(
    customer_name=data['customer_name'],
    Date=data['date'],
    products=products_str,
    recommended_products=recommended_products_str
)

print(formatted_email)



Dear AAHIL PETROLEUM INC,

I hope this email finds you well. We truly appreciate your continued trust in NEPA WHOLESALE for your product needs.

We noticed that you've recently purchased the following items from us on 2024-06-19:

• HQD PLUS 5% 1X6PK DISPOSABLE (1200) (Black Ice)
• REMARKABLE HERBS 8OZ POWDER (White Maeng Da)
• HQD BAR 5% 1X5PK DISPOSABLE (7000) (Cranberry Grape)
• SAVIA 12CT-500ML (Aloe Vera Mango)
...etc

Based on your preferences, we have curated a selection of products that we believe will perfectly complement and enhance your current offerings:

• ORION BAR 5% 1X5PK DISPOSABLE (10000) (KIWI PASSION FRUIT GUAVA)
• DUMMY XFINITY 5% 1X5PK DISPOSABLE (6900) (Bebe Berry)
• JELLY LIVE RESIN KO BLEND GUMMIES 1CT
• CLICKIT LIGHTER (GH-10877C) BOB MARLEY TORCH LIGHTER 15CT
• HALF BAKD 5-2 CONEZ (Sugar Cookie)
• SQUID 5K 5% 1X5PK DISPOSABLE (Blue Razz)
• LOST MARY 10PK 5% (OS5000) (Black Lemonade)
• CAKE HXC 5PK (Animal Cookies)
• TORCH ONYX 5PK UNICORN BUTTER
• VIRGINIA S

### 1.6 Defining the EMAIL GENERATING LLM

In [114]:

def Give_Email(femail):

    final_prompt = f"""
    You are an expert email generator.
    I will provide you with an email, and your task is to refine and enhance it to ensure
    it impresses the recipient. Your goal is to make the email compelling and clear, so the customer is highly likely
    to follow the instructions provided. Remember, each email needs to be unique, not similar to the others.
    Provide products and recommended products in a bullet point list, not in a paragraph. This is required.
    Make the language more human-like.
    Write in a natural, conversational tone that mimics human speech patterns.
    Vary sentence length and structure. Avoid overly perfect grammar or structure.
    Note: Do not make any changes to the date, previous purchased products, and recommended products.
    Paraphrase the original email naturally.

    dont forget to include previous purchase date

    {femail}
"""

    final_prompt = PromptTemplate.from_template(template=final_prompt)
 
    # Define the LLM chain
    llm_chain = LLMChain(
        llm=llm,
        prompt=final_prompt
    )
 
    # Run the LLM chain with the formatted prompt
    refined_email = llm_chain.invoke({'email': femail})
    email_content = refined_email['text']
   
   
    return email_content

In [118]:
mail_to_send=Give_Email(formatted_email)

### 1.7 Printing Final Mail

In [119]:
print(mail_to_send)

Hi AAHIL PETROLEUM INC,

I hope you're doing great! We're so grateful for your ongoing support.

We saw that you recently picked up some awesome stuff from us on June 19, 2024:

- HQD PLUS 5% 1X6PK DISPOSABLE (1200) (Black Ice)
- REMARKABLE HERBS 8OZ POWDER (White Maeng Da)
- HQD BAR 5% 1X5PK DISPOSABLE (7000) (Cranberry Grape)
- SAVIA 12CT-500ML (Aloe Vera Mango)
...and more

Based on what you've been digging, we've handpicked a few more products that we think you and your customers will love:

- ORION BAR 5% 1X5PK DISPOSABLE (10000) (KIWI PASSION FRUIT GUAVA)
- DUMMY XFINITY 5% 1X5PK DISPOSABLE (6900) (Bebe Berry)
- JELLY LIVE RESIN KO BLEND GUMMIES 1CT
- CLICKIT LIGHTER (GH-10877C) BOB MARLEY TORCH LIGHTER 15CT
- HALF BAKD 5-2 CONEZ (Sugar Cookie)
- SQUID 5K 5% 1X5PK DISPOSABLE (Blue Razz)
- LOST MARY 10PK 5% (OS5000) (Black Lemonade)
- CAKE HXC 5PK (Animal Cookies)
- TORCH ONYX 5PK UNICORN BUTTER
- VIRGINIA SLIMS 120'S BOX (Menthol Gold)

We're always here to help you find the best

# AUTOMATION FOR ALL CUSTOMERS

### ID LIST CREATING

In [216]:
id_list=df['customer_id'].unique()
# id_list=['22086.0','3207.0','14832.0']

In [217]:
print("The total number of Customers are: ",len(id_list))

The total number of Customers are:  589


In [232]:

results = []

def get_dict(llm, csv, ids):
    csv_agent = create_csv_agent(llm, csv, verbose=True, allow_dangerous_code=True)
   
    for id in ids:
        query = f"""
        Extract 'customer_id', 'customer_name', 'product', 'Recommended_products', 'customer_email', 'Date', 'last_purchased_month' 
        for 'customer_id' {id} and format it as a dictionary using df[df['customer_id'] == {id}].to_dict('records')[0].
        Ensure the resulting dictionary includes essential fields such as 'customer_name', 'Recommended_products', and 'customer_email'.
        """
       
        ans = csv_agent.invoke(query)
       
        model_output = ans['output']
 
        pattern = r"\{.*?\}"
 
        match = re.search(pattern, model_output)
       
        if match:
            dictionary_part = eval(match.group(0))  # Safely evaluate the dictionary part
            results.append(dictionary_part)
            
            file_path = 'output.txt'
            try:
                with open(file_path, 'a') as file:
                    data_str = str(dictionary_part)
                    file.write(data_str + '\n')  
                print(f"Data appended to {file_path}")
            except Exception as e:
                print(f"Error: {e}")

    return results
    
dictionary_parts = get_dict(llm, "ffinal_Emarketing.csv", Batch1)


### self agent

In [230]:
df =pd.read_csv("ffinal_Emarketing.csv")

In [251]:
data_dict = []

for index, row in df.iterrows():
    customer_dict = {
        'customer_id': row['customer_id'],
        'customer_name': row['customer_name'],
        'product': row['product'],
        'Recommended_products': row['Recommended_products'],
        'customer_email': row['customer_email'],
        'Date': row['date'],
        'last_purchased_month': row['last_purchased_month']
    }
    data_dict.append(customer_dict)

print(data_dict)


[{'customer_id': 11.0, 'customer_name': 'Angelo Difatta', 'product': 'HQD AIR 5% 1X5PK DISPOSABLE (4000) (Frozen Chocolate)', 'Recommended_products': 'FUME NICKY JAM 10PK (10000) (Summer Amante) , LOST MARY 5PK 5% (MO5000) (Ginger Bear) , SQUID 5K 5% 1X5PK DISPOSABLE (Blue Razz) , HQD AIR 5% 1X5PK DISPOSABLE (4000) (Cotton Candy) , FUME 10PK MINI 5% DISPOSABLE (600) (Tropical Fruit) , DUMMY VAPE 1% DUMMY DREAM 5 PK DISPOSABLE (8K)\n , HQD MAYA 5% 1X5PK DISPOSABLE (6000) (Strawberry Custard) , DEATH ROW 5000 5% 5PK DISPOSEABLE (Candy) , FUME 10PK RECHARGE 5% DISPOSABLE (5000) (Lemon Mint) , LOST MARY 10PK 5% (OS5000) (Pineapple Duo)', 'customer_email': 'angelo@nepawholesale.com', 'Date': '2024-02-19', 'last_purchased_month': 2}, {'customer_id': 14.0, 'customer_name': 'Nepa Wholesale', 'product': 'WISE TRASH BAG 10CT/26GALLON BLACK , NUTRAMENT 12/12OZ* (Strawberry)', 'Recommended_products': '.LOTY COCONUT WATER 24-500ML , LOTY JUICE 24-500ML (Lychee) , FLASH LIGHT 1 CT , WISE KITCHEN BAG

### Inspecting the Dictionary

In [252]:
j=0
for i in data_dict:
    j+=1
    print(i)
    print("\n")

print("There are ",j," items in the list")

{'customer_id': 11.0, 'customer_name': 'Angelo Difatta', 'product': 'HQD AIR 5% 1X5PK DISPOSABLE (4000) (Frozen Chocolate)', 'Recommended_products': 'FUME NICKY JAM 10PK (10000) (Summer Amante) , LOST MARY 5PK 5% (MO5000) (Ginger Bear) , SQUID 5K 5% 1X5PK DISPOSABLE (Blue Razz) , HQD AIR 5% 1X5PK DISPOSABLE (4000) (Cotton Candy) , FUME 10PK MINI 5% DISPOSABLE (600) (Tropical Fruit) , DUMMY VAPE 1% DUMMY DREAM 5 PK DISPOSABLE (8K)\n , HQD MAYA 5% 1X5PK DISPOSABLE (6000) (Strawberry Custard) , DEATH ROW 5000 5% 5PK DISPOSEABLE (Candy) , FUME 10PK RECHARGE 5% DISPOSABLE (5000) (Lemon Mint) , LOST MARY 10PK 5% (OS5000) (Pineapple Duo)', 'customer_email': 'angelo@nepawholesale.com', 'Date': '2024-02-19', 'last_purchased_month': 2}


{'customer_id': 14.0, 'customer_name': 'Nepa Wholesale', 'product': 'WISE TRASH BAG 10CT/26GALLON BLACK , NUTRAMENT 12/12OZ* (Strawberry)', 'Recommended_products': '.LOTY COCONUT WATER 24-500ML , LOTY JUICE 24-500ML (Lychee) , FLASH LIGHT 1 CT , WISE KITCHEN BAG

In [253]:
data_dict[:3]

[{'customer_id': 11.0,
  'customer_name': 'Angelo Difatta',
  'product': 'HQD AIR 5% 1X5PK DISPOSABLE (4000) (Frozen Chocolate)',
  'Recommended_products': 'FUME NICKY JAM 10PK (10000) (Summer Amante) , LOST MARY 5PK 5% (MO5000) (Ginger Bear) , SQUID 5K 5% 1X5PK DISPOSABLE (Blue Razz) , HQD AIR 5% 1X5PK DISPOSABLE (4000) (Cotton Candy) , FUME 10PK MINI 5% DISPOSABLE (600) (Tropical Fruit) , DUMMY VAPE 1% DUMMY DREAM 5 PK DISPOSABLE (8K)\n , HQD MAYA 5% 1X5PK DISPOSABLE (6000) (Strawberry Custard) , DEATH ROW 5000 5% 5PK DISPOSEABLE (Candy) , FUME 10PK RECHARGE 5% DISPOSABLE (5000) (Lemon Mint) , LOST MARY 10PK 5% (OS5000) (Pineapple Duo)',
  'customer_email': 'angelo@nepawholesale.com',
  'Date': '2024-02-19',
  'last_purchased_month': 2},
 {'customer_id': 14.0,
  'customer_name': 'Nepa Wholesale',
  'product': 'WISE TRASH BAG 10CT/26GALLON BLACK , NUTRAMENT 12/12OZ* (Strawberry)',
  'Recommended_products': '.LOTY COCONUT WATER 24-500ML , LOTY JUICE 24-500ML (Lychee) , FLASH LIGHT 1 CT

### below code contains the prompt which is further passed into llm with the shop data and the llm models generate the emails for those shops

In [256]:
li_formatted_email=[]

def mail_format(data_dict):
            
        j=0
        for i in data_dict:
    
            data=i

            mail_format = """
Dear {customer_name},

I hope this email finds you well. We truly appreciate your continued trust in NEPA WHOLESALE for your product needs.

We noticed that you've recently purchased the following items from us on {Date}:

{products}
...etc

Based on your preferences, we have curated a selection of products that we believe will perfectly complement and enhance your current offerings:

{recommended_products}

Our goal is to help you continue providing high-quality products to your customers and to support your business growth. Each of these recommendations has been carefully selected to ensure they align with your business needs and market demands.

If you have any questions or need further assistance, please don't hesitate to reach out. We're here to help you make the best choices for your business.

Thank you once again for choosing NEPA WHOLESALE. We look forward to continuing our successful partnership.

Best regards,

NEPA WHOLESALE LLC

"""

            # Split the products and recommended products into lists
            products_list = data['product'].split(' , ')
            recommended_products_list = data['Recommended_products'].split(' , ')

            # Add bullets to each item in the lists
            products_str = "\n".join(f"• {item}" for item in products_list)
            recommended_products_str = "\n".join(f"• {item}" for item in recommended_products_list)

            # Fill the placeholders in the email template
            formatted_email = mail_format.format(
                customer_name=data['customer_name'],
                Date=data['Date'],
                products=products_str,
                recommended_products=recommended_products_str
            )
            
            li_formatted_email.append(formatted_email)
           
            j+=1
            print("_"*150)
           
            print("Mail Format: ",j)
            print("_"*150)
        
            print(formatted_email)

            print("\n")


In [257]:
mail_format(data_dict)

______________________________________________________________________________________________________________________________________________________
Mail Format:  1
______________________________________________________________________________________________________________________________________________________

Dear Angelo Difatta,

I hope this email finds you well. We truly appreciate your continued trust in NEPA WHOLESALE for your product needs.

We noticed that you've recently purchased the following items from us on 2024-02-19:

• HQD AIR 5% 1X5PK DISPOSABLE (4000) (Frozen Chocolate)
...etc

Based on your preferences, we have curated a selection of products that we believe will perfectly complement and enhance your current offerings:

• FUME NICKY JAM 10PK (10000) (Summer Amante)
• LOST MARY 5PK 5% (MO5000) (Ginger Bear)
• SQUID 5K 5% 1X5PK DISPOSABLE (Blue Razz)
• HQD AIR 5% 1X5PK DISPOSABLE (4000) (Cotton Candy)
• FUME 10PK MINI 5% DISPOSABLE (600) (Tropical Fruit)
• DUMMY 

In [270]:

def Give_Email(femail):


    final_prompt = f"""
    You are an expert in paraphrasing emails. Your task is to refine and enhance the provided email to make it compelling and clear. The goal is to impress the recipient and encourage them to follow the provided instructions. Each email should be unique, avoiding repetition, and written in a natural, conversational tone that mimics human speech patterns.

    Important: Do not alter the date, previous purchased products, customer name, or recommended products. Paraphrase the original email naturally while retaining these details. Remember to list the previous purchases and recommended products in every email.

    Here is the email to paraphrase:

    {femail}
    """



    final_prompt = PromptTemplate.from_template(template=final_prompt)
        
     # Define the LLM chain
    llm_chain = LLMChain(
                llm=llm,
                prompt=final_prompt
            )
        
     # Run the LLM chain with the formatted prompt
    refined_email = llm_chain.invoke({'email': femail})
    email_content = refined_email['text']
        
        
    return email_content

In [272]:
final_emails = []
j=0
tot=len(li_formatted_email)
for i in li_formatted_email:
    j+=1
    tot-=1
    mail_to_send = Give_Email(i)
    file_path = 'mail_to_send.txt'

    try:
        with open(file_path, 'a') as file:
            data_str = str(mail_to_send)
            file.write("[")
            file.write(data_str + ',')  
            file.write("],\n\n\n")

            print(f"{j} Mail Created |......................................| {tot} Mail Left")
    except Exception as e:
        print(f"Error: {e}")

    final_emails.append(mail_to_send)

# Print the entire list of emails in the specified format
emails_str = ','.join(final_emails)
print(f"[{emails_str}]")


1 Mail Created |......................................| 588 Mail Left
2 Mail Created |......................................| 587 Mail Left
3 Mail Created |......................................| 586 Mail Left
4 Mail Created |......................................| 585 Mail Left
5 Mail Created |......................................| 584 Mail Left
6 Mail Created |......................................| 583 Mail Left
7 Mail Created |......................................| 582 Mail Left
8 Mail Created |......................................| 581 Mail Left
9 Mail Created |......................................| 580 Mail Left
10 Mail Created |......................................| 579 Mail Left
11 Mail Created |......................................| 578 Mail Left
12 Mail Created |......................................| 577 Mail Left
13 Mail Created |......................................| 576 Mail Left
14 Mail Created |......................................| 575 Mail Left
15 Mail Created

# putting mails inti dataframe

In [273]:
import pandas as pd

email_df = pd.DataFrame(final_emails, columns=['Emails'])

email_df.head()

Emails
0  Subject: Enhance Your Product Offerings with N...
1  Subject: Enhance Your Offerings with Our Tailo...
2  Subject: Enhance Your Product Offerings with O...
3  Subject: Enhance Your Product Offerings with O...
4  Dear BANDARI LLC,\n\nI hope this email finds y...

In [274]:

email_df.to_csv('final_emails.csv', index=False)

# inspecting the generated mails

In [275]:
j=0
for i in final_emails:
    
            j+=1
            print("_"*150)
           
            print("Final_Email: ",j)
            print("_"*150)
        
            print(i)

            print("\n")

______________________________________________________________________________________________________________________________________________________
Final_Email:  1
______________________________________________________________________________________________________________________________________________________
Subject: Enhance Your Product Offerings with NEPA WHOLESALE's Expert Recommendations

Dear Angelo Difatta,

We hope this email finds you in good spirits. We're delighted to have you as a valued customer at NEPA WHOLESALE.

We've noticed your recent purchases from us on February 19, 2024, including:

• HQD AIR 5% 1X5PK DISPOSABLE (4000) (Frozen Chocolate)
...etc

To help you expand your offerings and cater to your customers' evolving preferences, we've handpicked a selection of products that we believe will complement your current inventory:

• FUME NICKY JAM 10PK (10000) (Summer Amante)
• LOST MARY 5PK 5% (MO5000) (Ginger Bear)
• SQUID 5K 5% 1X5PK DISPOSABLE (Blue Razz)
• H